# **Rule-Based Algorithm**
### Group 1 - Detection of Negation and Uncertainty

- Marino Oliveros Blanco NIU:1668563
- 
- 
- 

**Data loading**

In [1]:
# Libraries
import json
import re
from langdetect import detect # Library for language detection
from spellchecker import SpellChecker
import spacy
import string

OSError: [WinError 126] The specified module could not be found. Error loading "c:\Languages and Environments\Python 3.12.3\Lib\site-packages\torch\lib\fbgemm.dll" or one of its dependencies.

In [346]:
'''
# Loading the json file
loading = open("negacio_train_v2024.json")
training_data = json.load(loading)
'''

'\n# Loading the json file\nloading = open("negacio_train_v2024.json")\ntraining_data = json.load(loading)\n'

### **Pre-processing**
- Removing redacted entries
- Removing language mixes
- Solving misspelled words
- Removing patient information
- Tokenizing 

In [347]:
'''
# 1 Remove pacient information and redacted entries
def remove_pacient_info(text):
    # Remove lines starting with "nº historia clinica:" and ending with "motiu d'ingres"
    text = re.sub(r'nº historia clinica:.*?motiu d\'ingres', '', text, flags=re.DOTALL)
    # Remove lines starting with "nhc" and ending with "lopd"
    text = re.sub(r'nhc.*?lopd', '', text, flags=re.DOTALL)
    # Remove all asterisks '*'
    text = text.replace('*', '')
    return text


# 2 Remove Punctuation (Able to be turned ON/OFF)
def remove_punctuation(text):
    # Define a translation table to map punctuation to None
    translator = str.maketrans('', '', string.punctuation)
    # Remove punctuation using the translation table
    text = text.translate(translator)
    return text


# 3 Spell cheking with language detection (Able to be turned ON/OFF)
# Load language models for Spanish and Catalan
nlp_es = spacy.load("es_core_news_sm")
nlp_ca = spacy.load("ca_core_news_sm")

def spell_check_and_lemmatize(text):
    # Detect the language of the text
    language = detect(text)
    # Initialize spell checker
    spell = SpellChecker(language='es')  # As most of the text is in Spanish

    # Tokenize the text using the appropriate language model
    if language == 'ca':
        doc = nlp_ca(text)
    else:
        doc = nlp_es(text)

    # Correct misspelled words and lemmatize tokens
    corrected_tokens = []
    for token in doc:
        # Check if the token is a punctuation or whitespace
        if not token.is_punct and not token.is_space:
            # Get the corrected version of the token
            corrected_token = spell.correction(token.text)
            # Lemmatize the corrected token
            corrected_token_lemma = token.lemma_ if token.lemma_ != '-PRON-' else corrected_token
            corrected_tokens.append(corrected_token_lemma)
        else:
            corrected_tokens.append(token.text)

    # Join the tokens back into text
    corrected_text = ' '.join(corrected_tokens)
    return corrected_text


# 4 Tokenization with coordinates of the original text for (evaluation)
def tokenize_with_coordinates(text):
    # Tokenize the text while preserving the coordinates
    tokens_with_coordinates = []
    token_start = 0
    for token in re.finditer(r'\S+', text):
        token_text = token.group(0)
        token_end = token_start + len(token_text)
        tokens_with_coordinates.append((token_text, token_start, token_end))
        # Update token start position for the next token
        token_start = token_end
    return tokens_with_coordinates


# Main function to process the text
def pre_process_text(text, remove_punctuation_call=True, spell_check_call=True):
    
    # 1 Remove pacient information and redacted entries
    preprocessed_text = remove_pacient_info(text)

    # 2 Remove punctuation if specified
    if remove_punctuation_call:
        preprocessed_text = remove_punctuation(preprocessed_text)

    # 3 Spell check and lemmatize if specified
    if spell_check_call:
        preprocessed_text = spell_check_and_lemmatize(preprocessed_text)

    # 4 Tokenize the text with coordinates
    tokens_with_coordinates = tokenize_with_coordinates(preprocessed_text)

    return tokens_with_coordinates
'''

'\n# 1 Remove pacient information and redacted entries\ndef remove_pacient_info(text):\n    # Remove lines starting with "nº historia clinica:" and ending with "motiu d\'ingres"\n    text = re.sub(r\'nº historia clinica:.*?motiu d\'ingres\', \'\', text, flags=re.DOTALL)\n    # Remove lines starting with "nhc" and ending with "lopd"\n    text = re.sub(r\'nhc.*?lopd\', \'\', text, flags=re.DOTALL)\n    # Remove all asterisks \'*\'\n    text = text.replace(\'*\', \'\')\n    return text\n\n\n# 2 Remove Punctuation (Able to be turned ON/OFF)\ndef remove_punctuation(text):\n    # Define a translation table to map punctuation to None\n    translator = str.maketrans(\'\', \'\', string.punctuation)\n    # Remove punctuation using the translation table\n    text = text.translate(translator)\n    return text\n\n\n# 3 Spell cheking with language detection (Able to be turned ON/OFF)\n# Load language models for Spanish and Catalan\nnlp_es = spacy.load("es_core_news_sm")\nnlp_ca = spacy.load("ca_core

In [348]:
# Load language models for Spanish and Catalan
nlp_es = spacy.load("es_core_news_sm")
nlp_ca = spacy.load("ca_core_news_sm")

def remove_patient_info(tokens):
    # Define patterns to match patient information identifiers
    patterns = [
        r'nº\s?historia\s?clinica:',
        r'nºepisodi:',
        r'sexe:',
        r'data\s?de\s?naixement:',
        r'edat:',
        r'procedencia',
        r'servei\s?obstetricia',
        r'data\sd\'ingres',
        r'data\sd\'alta',
        r'ates\s?per',
        r'informe\sd\'alta\sd\'hospitalitzacio',
        r'motiu\sd\'ingres',
        r'nhc',
        r'lopd'
    ]
    # Join tokens into text for efficient pattern matching
    text = ' '.join([token[0] for token in tokens])
    # Remove tokens containing patient information identifiers
    for pattern in patterns:
        text = re.sub(pattern + '.*?(?=\\s|$)', '', text, flags=re.IGNORECASE)
    # Tokenize the modified text
    return tokenize_with_coordinates(text)


# 2 Remove Punctuation (Able to be turned ON/OFF)
def remove_punctuation(tokens):
    # Remove punctuation from token text
    tokens_without_punct = [(token[0].translate(str.maketrans('', '', string.punctuation)), token[1], token[2]) for token in tokens]
    return tokens_without_punct

# 3 Spell checking with language detection (Able to be turned ON/OFF)
def spell_check_and_lemmatize(tokens):
    # Join tokens into text
    text = ' '.join([token[0] for token in tokens])
    # Detect the language of the text
    language = detect(text)
    # Initialize spell checker
    spell = SpellChecker(language='es')  # As most of the text is in Spanish

    # Tokenize the text using the appropriate language model
    if language == 'ca':
        doc = nlp_ca(text)
    else:
        doc = nlp_es(text)

    # Correct misspelled words and lemmatize tokens
    corrected_tokens = []
    for token in doc:
        # Check if the token is a punctuation or whitespace
        if not token.is_punct and not token.is_space:
            # Get the corrected version of the token
            corrected_token = spell.correction(token.text)
            # Lemmatize the corrected token
            corrected_token_lemma = token.lemma_ if token.lemma_ != '-PRON-' else corrected_token
            corrected_tokens.append((corrected_token_lemma, token.idx, token.idx + len(corrected_token_lemma)))
        else:
            corrected_tokens.append((token.text, token.idx, token.idx + len(token.text)))

    return corrected_tokens

# 4 Tokenization with coordinates of the original text for (evaluation)
def tokenize_with_coordinates(text):
    # Tokenize the text while preserving the coordinates
    tokens_with_coordinates = []
    token_start = 0
    for token in re.finditer(r'\S+', text):
        token_text = token.group(0)
        token_end = token_start + len(token_text)
        tokens_with_coordinates.append((token_text, token_start, token_end))
        # Update token start position for the next token
        token_start = token_end
    return tokens_with_coordinates

# Remove empty tokens   
def remove_empty_tokens(tokens):
    # Filter out tokens with empty text
    non_empty_tokens = [(token[0], token[1], token[2]) for token in tokens if token[0]]
    return non_empty_tokens


# Main function to process the text
def pre_process_text(text, remove_punctuation_call=True, spell_check_call=True):
    # Tokenize the text with coordinates
    tokens_with_coordinates = tokenize_with_coordinates(text)

    # Apply each processing step to the tokens
    if remove_punctuation_call:
        tokens_with_coordinates = remove_punctuation(tokens_with_coordinates)

    if spell_check_call:
        tokens_with_coordinates = spell_check_and_lemmatize(tokens_with_coordinates)

    # Remove empty tokens
    tokens_with_coordinates = remove_empty_tokens(tokens_with_coordinates)

    # Remove  extra patient information
    tokens_with_coordinates = tokens_with_coordinates[32:] #nº-motiu
    tokens_with_coordinates = tokens_with_coordinates[:-5] #nhc-lopd

    # Return the modified tokens
    return tokens_with_coordinates


Real Usage

In [349]:
# Load the JSON file
with open("negacio_train_v2024.json", "r", encoding="utf-8") as file:
    training_data = json.load(file)

# List to store processed texts
processed_texts = []

# Iterate over each entry in the training data
for entry in training_data:
    text = entry["data"]["text"]  # Extract the text from the JSON object
    processed_text = pre_process_text(text, remove_punctuation_call=True, spell_check_call=False)
    processed_texts.append(processed_text)

# Printing (not necessary)
for processed_text in processed_texts:
    for token, start, end in processed_text:
        print(f"Token: {token}, Start: {start}, End: {end}")

Token: dingres, Start: 265, End: 273
Token: paciente, Start: 273, End: 281
Token: que, Start: 281, End: 284
Token: ingresa, Start: 284, End: 291
Token: de, Start: 291, End: 293
Token: forma, Start: 293, End: 298
Token: programada, Start: 298, End: 308
Token: para, Start: 308, End: 312
Token: realizacion, Start: 312, End: 323
Token: de, Start: 323, End: 325
Token: uretrotomia, Start: 325, End: 336
Token: interna, Start: 336, End: 343
Token: antecedents, Start: 344, End: 355
Token: alergia, Start: 355, End: 362
Token: a, Start: 362, End: 363
Token: penicilina, Start: 363, End: 373
Token: y, Start: 373, End: 374
Token: cloramfenicol, Start: 374, End: 387
Token: no, Start: 388, End: 390
Token: habitos, Start: 390, End: 397
Token: toxicos, Start: 397, End: 405
Token: antecedentes, Start: 405, End: 417
Token: medicos, Start: 417, End: 425
Token: bloqueo, Start: 425, End: 432
Token: auriculoventricular, Start: 432, End: 451
Token: de, Start: 451, End: 453
Token: primer, Start: 453, End: 459
T

In [350]:
print(processed_text)
print(processed_texts[100])
print(processed_texts[120])
print(processed_texts[20])

[('motiu', 243, 248), ('dingres', 248, 256), ('paciente', 256, 264), ('de', 264, 266), ('8', 266, 267), ('años', 267, 271), ('que', 271, 274), ('ingresa', 274, 281), ('el', 281, 283), ('dia', 283, 286), ('08102019', 286, 296), ('en', 296, 298), ('planta', 298, 304), ('de', 304, 306), ('hospitalizacion', 306, 321), ('de', 321, 323), ('pediatria', 323, 332), ('por', 332, 335), ('sindrome', 335, 343), ('febril', 343, 350), ('antecedents', 350, 361), ('no', 361, 363), ('alergias', 363, 371), ('conocidas', 371, 381), ('calendario', 381, 391), ('vacunal', 391, 398), ('al', 398, 400), ('dia', 400, 404), ('antecedentes', 404, 416), ('patologicos', 416, 428), ('en', 429, 431), ('seguimiento', 431, 442), ('por', 442, 445), ('cardiologia', 445, 456), ('por', 456, 459), ('ligera', 459, 465), ('hipertrofia', 465, 476), ('ventricular', 476, 487), ('en', 487, 489), ('los', 489, 492), ('primeros', 492, 500), ('años', 500, 504), ('de', 504, 506), ('vida', 506, 511), ('estudio', 511, 518), ('cardiologic

**Pre-processing json object**

- Reading the json object to obtain a list of the Negation and Uncertainty proc words as well as their scopes

- The scopes and annotations will be used for the supervised learning as the 'target'

In [351]:
# Loading the json object
loading = open("negacio_train_v2024.json")
for_object = loading.read()
object = json.loads(for_object)

In [352]:
# Prepare lists to store the results
negations = []
negation_scopes = []
uncertainties = []
uncertainty_scopes = []

# Process the documents and obtain negation and uncertainty annotations
for item in object:
    text_data = item['data']['text']
    for prediction in item['predictions']:
        for result in prediction['result']:
            labels = result['value']['labels']
            start_index = result['value']['start']
            end_index = result['value']['end']
            text_segment = item['data']['text'][start_index:end_index]

            if "NEG" in labels:
                negations.append(text_segment)

                # Find the scope of the negation
                scope_start = -1
                scope_end = -1

                # Search for the scope starting just after the negation
                current_index = prediction['result'].index(result)
                if current_index < len(prediction['result']) - 1:
                    next_result = prediction['result'][current_index + 1]
                    next_start = next_result['value']['start']
                    next_end = next_result['value']['end']
                    next_labels = next_result['value']['labels']
                    if "NSCO" in next_labels and next_start == end_index:
                        scope_start = next_start
                        scope_end = next_end

                current_index = prediction['result'].index(result)
                if current_index > 0:
                    prev_result = prediction['result'][current_index - 1]
                    prev_start = prev_result['value']['start']
                    prev_end = prev_result['value']['end']
                    prev_labels = prev_result['value']['labels']
                    if "NSCO" in prev_labels and prev_end == start_index:
                        scope_start = prev_start
                        scope_end = prev_end

                if scope_start != -1 and scope_end != -1:
                    scope_text = item['data']['text'][scope_start:scope_end]
                    negation_scopes.append((start_index, scope_end))

            if "UNC" in labels:
                uncertainties.append(text_segment)

                # Find the scope of the uncertainty
                scope_start = -1
                scope_end = -1

                # Search for the scope starting just after the uncertainty
                current_index = prediction['result'].index(result)
                if current_index < len(prediction['result']) - 1:
                    next_result = prediction['result'][current_index + 1]
                    next_start = next_result['value']['start']
                    next_end = next_result['value']['end']
                    next_labels = next_result['value']['labels']
                    if "USCO" in next_labels and next_start == end_index:
                        scope_start = next_start
                        scope_end = next_end

                current_index = prediction['result'].index(result)
                if current_index > 0:
                    prev_result = prediction['result'][current_index - 1]
                    prev_start = prev_result['value']['start']
                    prev_end = prev_result['value']['end']
                    prev_labels = prev_result['value']['labels']
                    if "USCO" in prev_labels and prev_end == start_index:
                        scope_start = prev_start
                        scope_end = prev_end

                if scope_start != -1 and scope_end != -1:
                    scope_text = item['data']['text'][scope_start:scope_end]
                    uncertainty_scopes.append((start_index, scope_end))

# Remove duplicates from the annotation lists
negations = list(set(negations))
negation_scopes = list(set(negation_scopes))
uncertainties = list(set(uncertainties))
uncertainty_scopes = list(set(uncertainty_scopes))

# Print the negation/uncertainty annotations and their scopes
print("Negations\n", negations)
print("Negation Scopes\n", negation_scopes)
print("Uncertainties\n", uncertainties)
print("Uncertainty Scopes\n", uncertainty_scopes)

Negations
 ['ninguno ', 'negaitvo', 'ex ', 'no ', 'negativas', ' negativo', 'asintomatico ', 'en ninguna ', 'negativos,', 'negativa,', 'excepto ', 'ceden ', 'imposibilidad', 'ausencia de ', 'niega', 'negativos;', 'irregulares', 'ex fumador ', 'se suspende ', 'neg;', 'imposibilidad de ', 'negatividad de ', 'neg,', ' afebril', 'niega ', 'desaparecen ', 'ex', 'rechaza ', 'nega', 'asintomatica,', 'negativos ', 'niegan ', 'inespecificos ', 'afebril ', 'negativa ', 'inestabilidad ', 'asintomatico,', 'desaparicion de ', 'negatividad ', 'desaparicion del ', 'impide ', 'negatiu.', 'falta de ', 'retirar ', 'neg.', 'inespecifico:', 'negativa.', 'desorientado ', 'afebril.', 'negativo,', 'sin ', 'se desestimo ', 'negativos.', 'inespecifico.', 'asintomatica', 'sense', 'negatividad del ', 'indetectable.', 'se retira ', 'cede ', 'inespecifico', 'arritmicos', 'afebril', 'descartada ', 'asintomatico', 'neg', 'sin', 'desorientacion.', 'exfumador ', 'negativa', 'atipicos', ' no ', 'sense ', 'negativa)', '

**Implementation**

In [353]:

# We can use any of the following methods to detect negation or uncertainty in a sentence

#Pre-defined list of negation trigger words
#Regular expressions
#Part of Speech tagging
#Syntactic parsing

**Results**

In [354]:
# Explore the results



In [355]:
# Pre negation in 'es'
neg_pre_es = [
    "impide",
    "ausencia de",
    "no pueden ver",
    "no poder",
    "revisado para",
    "niega",
    "negando",
    "evaluar por",
    "no revela",
    "libre de",
    "negativo para",
    "nunca desarrollado",
    "nunca tuve",
    "no",
    "no anormal",
    "ninguna causa de",
    "sin quejas de",
    "sin evidencia",
    "ninguna nueva evidencia",
    "ninguna otra evidencia",
    "ninguna evidencia para sugerir",
    "sin hallazgos de",
    "no hay hallazgos para indicar",
    "no hay evidencia mamográfica de",
    "nada nuevo",
    "ninguna evidencia radiográfica de",
    "ninguna señal de",
    "no significativo",
    "ninguna sugerencia de",
    "no sospechoso",
    "no aparece",
    "no apreciar",
    "no asociado con",
    "no me quejo de",
    "no demostrar",
    "no exhibir",
    "no sentir",
    "no tenía",
    "no tengo",
    "no saber de",
    "no se sabe que tiene",
    "no revelar",
    "paciente no era",
    "más bien que",
    "resuelto",
    "hacer una prueba por",
    "excluir",
    "nada especial para",
    "con ningún",
    "sin ninguna evidencia de",
    "sin evidencia",
    "sin indicación de",
    "sin signo de",
    "sin",
    "descartar para",
    "descartarlo por",
    "descartarla por",
    "descartar al paciente por",
    "descartarlo",
    "descartarla",
    "descartar",
    "r / o",
    "ro",
    "descartar al paciente",
    "excluye",
    "lo descarta",
    "la excluye",
    "expulsó al paciente por",
    "gobierna al paciente",
    "lo descartó contra",
    "la descartó contra",
    "lo descartó",
    "la descartó",
    "descartado contra",
    "descartó al paciente contra",
    "descartaron para",
    "descartaron contra",
    "descartó",
    "lo descartaron por",
    "lo descartaron en contra",
    "la descartaron por",
    "lo descartó contra",
    "lo descartó",
    "descartaron al paciente contra",
    "descartaron al paciente por",
    "descartó al paciente",
    "puede descartar",
    "puede descartar contra",
    "puede descartar",
    "puede descartarlo por",
    "puede descartarlo en contra",
    "puede descartarlo",
    "puede descartarla por",
    "puede descartarla contra",
    "puede descartarla",
    "puede descartar al paciente por",
    "puede descartar al paciente contra",
    "puede descartar al paciente",
    "adecuado para descartarlo por",
    "adecuado para descartarlo",
    "adecuado para descartarla por",
    "adecuado para descartarla",
    "adecuado para descartar al paciente por",
    "adecuado para descartar al paciente contra",
    "adecuado para descartar al paciente",
    "suficiente para descartar",
    "suficiente para descartar",
    "suficiente para descartar",
    "suficiente para descartarlo por",
    "suficiente para descartarlo en contra",
    "suficiente para descartarla por",
    "suficiente para descartarla en contra",
    "suficiente para descartar al paciente por",
    "suficiente para descartar al paciente contra",
    "suficiente para descartar al paciente",
    "lo que debe descartarse es"
]

# Post negation in 'es'
neg_post_es = [
    "rechazado",
    "declina",
    "negado",
    "no ver",
    "no ser",
    "suficiente para descartarla",
    "suficiente para descartarlo",
    "adecuado para descartar",
    "lo descartaron",
    "debe descartarse para",
    "debe ser descartado para",
    "puede ser descartado para",
    "puede ser descartado para",
    "podría ser descartado por",
    "será descartado por",
    "se puede descartar por",
    "debe descartarse para",
    "debe ser descartado por",
    "ser descartado por",
    "improbable",
    "libre",
    "fue descartado",
    "está descartado",
    "están descartadas",
    "han sido descartadas",
    "ha sido descartado",
    "siendo descartado",
    "debe descartarse",
    "debe ser descartado",
    "puede ser descartado",
    "podría descartarse",
    "podría ser descartado",
    "será descartado",
    "se puede descartar",
    "debe descartarse",
    "debe ser descartado",
    "ser descartado",
    "se descarta"
]


# Pre negation in 'ca'
neg_pre_ca = [
 "absència de",
 "no poden veure",
 "no poder",
 "revisat per a",
 "nega",
 "negant",
 "avaluar per",
 "no revela",
 "lliure de",
 "negatiu per a",
 "mai desenvolupat",
 "mai vaig tenir",
 "no",
 "no anormal",
 "cap causa de",
 "sense queixes de",
 "sense evidència",
 "cap nova evidència",
 "cap altra evidència",
 "cap evidència per a suggerir",
 "sense troballes de",
 "no hi ha troballes per a indicar",
 "no hi ha evidència mamogràfica de",
 "res nou",
 "cap evidència radiogràfica de",
 "cap senyal de",
 "no significatiu",
 "cap suggeriment de",
 "no sospitós",
 "no apareix",
 "no apreciar",
 "no associat amb",
 "no em queixo de",
 "no demostrar",
 "no exhibir",
 "no sentir",
 "no tenia",
 "no tinc",
 "no saber de",
 "no se sap que té",
 "no revelar",
 "pacient no era",
 "més aviat que",
 "resolt",
 "fer una prova per",
 "excloure",
 "gens especial per a",
 "amb cap",
 "sense cap evidència de",
 "sense evidència",
 "sense indicació de",
 "sense signe de",
 "sense",
 "descartar per a",
 "descartar-ho per",
 "descartar-la per",
 "descartar al pacient per",
 "descartar-ho",
 "descartar-la",
 "descartar",
 "r / o",
 "ro",
 "descartar al pacient",
 "exclou",
 "ho descarta",
 "l'exclou",
 "va expulsar al pacient per",
 "governa al pacient",
 "ho va descartar contra",
 "la va descartar contra",
 "ho va descartar",
 "la va descartar",
 "descartat contra",
 "va descartar al pacient contra",
 "van descartar per a",
 "van descartar contra",
 "va descartar",
 "ho van descartar per",
 "ho van descartar en contra",
 "la van descartar per",
 "ho va descartar contra",
 "ho va descartar",
 "van descartar al pacient contra",
 "van descartar al pacient per",
 "va descartar al pacient",
 "pot descartar",
 "pot descartar contra",
 "pot descartar",
 "pot descartar-ho per",
 "pot descartar-ho en contra",
 "pot descartar-ho",
 "pot descartar-la per",
 "pot descartar-la contra",
 "pot descartar-la",
 "pot descartar al pacient per",
 "pot descartar al pacient contra",
 "pot descartar al pacient",
 "adequat per a descartar-lo per",
 "adequat per a descartar-lo",
 "adequat per a descartar-la per",
 "adequat per a descartar-la",
 "adequat per a descartar al pacient per",
 "adequat per a descartar al pacient contra",
 "adequat per a descartar al pacient",
 "suficient per a descartar",
 "suficient per a descartar",
 "suficient per a descartar",
 "suficient per a descartar-lo per",
 "suficient per a descartar-lo en contra",
 "suficient per a descartar-la per",
 "suficient per a descartar-la en contra",
 "suficient per a descartar al pacient per",
 "suficient per a descartar al pacient contra",
 "suficient per a descartar al pacient",
 "la qual cosa ha de descartar-se és"
]

 #Post negation in 'cs'
neg_post_ca = [
 "rebutjat",
 "declina",
 "negat",
 "no veure",
 "no ser",
 "suficient per a descartar-la",
 "suficient per a descartar-ho",
 "adequat per a descartar",
 "ho van descartar",
 "ha de descartar-se per a",
 "ha de ser descartat per a",
 "pot ser descartat per a",
 "pot ser descartat per a",
 "podria ser descartat per",
 "serà descartat per",
 "es pot descartar per",
 "ha de descartar-se per a",
 "ha de ser descartat per",
 "ser descartat per",
 "improbable",
 "lliure",
 "va ser descartat",
 "està descartat",
 "estan descartades",
 "han estat descartades",
 "ha estat descartat",
 "sent descartat",
 "ha de descartar-se",
 "ha de ser descartat",
 "pot ser descartat",
 "podria descartar-se",
 "podria ser descartat",
 "serà descartat",
 "es pot descartar",
 "ha de descartar-se",
 "ha de ser descartat",
 "ser descartat",
 "es descarta"
]

In [356]:
# Lemma version of the negation trigger words

# Pre negation in 'es'
neg_pre_es_lemma = [
    "ausenci de",
    "no pued ver",
    "no pod",
    "revis par",
    "rechaz",
    "declin",
    "neg",
    "nieg",
    "neg",
    "evalu por",
    "no revel",
    "libr de",
    "negat par",
    "nunc desarroll",
    "nunc tuv",
    "no",
    "no anormal",
    "ningun caus de",
    "sin quej de",
    "sin evident",
    "ningun nuev evident",
    "ningun otra evident",
    "ningun evident par sug",
    "sin hallazg de",
    "no hay hallazg par indic",
    "no hay evident mamograf de",
    "nad nuev",
    "ningun evident radiograf de",
    "ningun señal de",
    "no signific",
    "sin sign de",
    "ningun sugerent de",
    "no sospech",
    "no",
    "no aparec",
    "no apreci",
    "no asoci con",
    "no me quej de",
    "no demostr",
    "no exhib",
    "no sent",
    "no ten",
    "no teng",
    "no sab de",
    "no se sab que tien",
    "no revel",
    "no ver",
    "no ser",
    "pacient no era",
    "mas bien que",
    "resuelt",
    "hac una prueb por",
    "exclu",
    "nad especial par",
    "con ningun",
    "sin ningun evident de",
    "sin evident",
    "sin indic de",
    "sin sign de",
    "sin",
    "descart par",
    "descart por",
    "descart por",
    "descart al pacient por",
    "descart",
    "descart",
    "descart",
    "r / o",
    "ro",
    "descart al pacient",
    "exclu",
    "lo descart",
    "la exclu",
    "expuls al pacient por",
    "gobiern al pacient",
    "lo descart contr",
    "la descart contr",
    "lo descart",
    "la descart",
    "descart contr",
    "descart al pacient contr",
    "descart par",
    "descart contr",
    "descart",
    "lo descart por",
    "lo descart en contr",
    "lo descart",
    "la descart por",
    "lo descart contr",
    "lo descart",
    "descart al pacient contr",
    "descart al pacient por",
    "descart al pacient",
    "pued descart",
    "pued descart contr",
    "pued descart",
    "pued descart por",
    "pued descart en contr",
    "pued descart",
    "pued descart por",
    "pued descart contr",
    "pued descart",
    "pued descart al pacient por",
    "pued descart al pacient contr",
    "pued descart al pacient",
    "adecu par descart",
    "adecu par descart",
    "adecu par descart por",
    "adecu par descart",
    "adecu par descart por",
    "adecu par descart",
    "adecu par descart al pacient por",
    "adecu par descart al pacient contr",
    "adecu par descart al pacient",
    "suficient par descart",
    "suficient par descart",
    "suficient par descart",
    "suficient par descart por",
    "suficient par descart en contr",
    "suficient par descart",
    "suficient par descart por",
    "suficient par descart en contr",
    "suficient par descart",
    "suficient par descart al pacient por",
    "suficient par descart al pacient contr",
    "suficient par descart al pacient",
    "lo que deb descart es"
]

neg_post_es_lemma = [
    "deb descart par",
    "deb ser descart par",
    "pued ser descart par",
    "pued ser descart par",
    "podr ser descart por",
    "ser descart por",
    "se pued descart por",
    "deb descart par",
    "deb ser descart por",
    "ser descart por",
    "improb",
    "libr",
    "fue descart",
    "esta descart",
    "estan descart",
    "han sid descart",
    "ha sid descart",
    "siend descart",
    "deb descart",
    "deb ser descart",
    "pued ser descart",
    "podr descart",
    "podr ser descart",
    "ser descart",
    "se pued descart",
    "deb descart",
    "deb ser descart",
    "ser descart",
    "se descart"
]